sql practice using pandas query <br>
create sqlite database from csv <br>
data from kaggle <br>

In [54]:
import sqlite3
import csv
import pandas as pd

## Exploratory Data Analysis

In [55]:
comments_df = pd.read_csv('comments.csv')
#comments_df.head()

In [56]:
comments_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18409 entries, 0 to 18408
Data columns (total 5 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   Unnamed: 0  18409 non-null  int64  
 1   Video ID    18409 non-null  object 
 2   Comment     18408 non-null  object 
 3   Likes       18409 non-null  float64
 4   Sentiment   18409 non-null  float64
dtypes: float64(2), int64(1), object(2)
memory usage: 719.2+ KB


In [57]:
comments_df[comments_df.Comment.isna()]

Unnamed: 0     Video ID Comment  Likes  Sentiment
9745        9745  bvkk3UdlfA4     NaN    1.0        1.0

In [58]:
videos_stats_df = pd.read_csv('videos-stats.csv')
#videos_stats_df.head()

In [59]:
videos_stats_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1881 entries, 0 to 1880
Data columns (total 8 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   Unnamed: 0    1881 non-null   int64  
 1   Title         1881 non-null   object 
 2   Video ID      1881 non-null   object 
 3   Published At  1881 non-null   object 
 4   Keyword       1881 non-null   object 
 5   Likes         1879 non-null   float64
 6   Comments      1879 non-null   float64
 7   Views         1879 non-null   float64
dtypes: float64(3), int64(1), object(4)
memory usage: 117.7+ KB


In [60]:
videos_stats_df[videos_stats_df.Likes.isna()]

Unnamed: 0                             Title     Video ID Published At  \
1879        1879         What is Machine Learning?  f_uwKZIAeM0   2017-01-11   
1880        1880  Don&#39;t learn machine learning  cyLWtMSry58   2020-03-30   

               Keyword  Likes  Comments  Views  
1879  machine learning    NaN       NaN    NaN  
1880  machine learning    NaN       NaN    NaN

## Set up Sqlite Database

### Table : videos_stats

In [61]:
# Create connection and cursor object
conn = sqlite3.connect('YouTube_Stats.db')
cursor = conn.cursor()

In [62]:
# Create table from csv file
with open('videos-stats.csv', 'r') as file:
    reader = csv.reader(file)
    header_1 = next(reader)
    
    # add column name to first column
    if not header_1[0]:
        header_1[0] = 'Index'
    
    # replace space with _ in column names
    header_1 = [col.replace(' ', '_') for col in header_1]
    header_1[0] = f'"{header_1[0]}"'

    # create table with column names and data types
    create_table_query = f'''
        CREATE TABLE IF NOT EXISTS videos_stats (
            {header_1[0]} INTEGER,
            {header_1[1]} TEXT,
            {header_1[2]} VARCHAR,
            {header_1[3]} DATE,
            {header_1[4]} VARCHAR,
            {header_1[5]} FLOAT,
            {header_1[6]} FLOAT,
            {header_1[7]} FLOAT
        )
    '''

    # execute query
    cursor.execute(create_table_query)

In [63]:
# Input data from csv file
with open('videos-stats.csv', 'r') as file:
    reader = csv.reader(file)
    next(reader)

    # create strings for insert queries
    # concatenate column names with ', ' as separator
    columns = ', '.join(header_1)
    # concatenate len(header) of '?' with ', ' as separator
    question_marks = ', '.join(['?'] * len(header_1))

    # insert data
    for row in reader:
        insert_query = f'INSERT INTO videos_stats ({columns}) VALUES ({question_marks})'
        cursor.execute(insert_query, row)
    
    # commit changes
    conn.commit()

In [65]:
# Fill missing values in 'Likes', 'Comments', and 'Views' with 0's
columns_fill_na = [header_1[5], header_1[6], header_1[7]]
print(columns_fill_na)

for col in columns_fill_na:
    update_query = f'''
        UPDATE videos_stats
        SET {col} = 0.0
        WHERE {col} = ''
    '''

    cursor.execute(update_query)

conn.commit()

In [66]:
# Print table
cursor.execute('SELECT * FROM videos_stats')
#cursor.execute('PRAGMA table_info(videos_stats)')
rows = cursor.fetchall()
for row in rows:
    print(row)

(0, 'Apple Pay Is Killing the Physical Wallet After Only Eight Years | Tech News Briefing Podcast | WSJ', 'wAZZ-UWGVHI', '2022-08-23', 'tech', 3407.0, 672.0, 135612.0)
(1, 'The most EXPENSIVE thing I own.', 'b3x28s61q3c', '2022-08-24', 'tech', 76779.0, 4306.0, 1758063.0)
(2, 'My New House Gaming Setup is SICK!', '4mgePWWCAmA', '2022-08-23', 'tech', 63825.0, 3338.0, 1564007.0)
(3, 'Petrol Vs Liquid Nitrogen | Freezing Experiment | പെട്രോളിനെ ഐസ് ആകാൻ പറ്റുമോ | M4 Tech |', 'kXiYSI7H2b0', '2022-08-23', 'tech', 71566.0, 1426.0, 922918.0)
(4, 'Best Back to School Tech 2022!', 'ErMwWXQxHp0', '2022-08-08', 'tech', 96513.0, 5155.0, 1855644.0)
(5, 'Brewmaster Answers Beer Questions From Twitter | Tech Support | WIRED', '18fwz9Itbvo', '2021-11-05', 'tech', 33570.0, 1643.0, 943119.0)
(6, 'Tech Monopolies: Last Week Tonight with John Oliver (HBO)', 'jXf04bhcjbg', '2022-06-13', 'tech', 135047.0, 9367.0, 5937790.0)
(7, 'I bought the STRANGEST TECH on the Internet.', '2TqOmtTAMRY', '2022-08-07', 'tec

### Table : comments

In [67]:
# Create table from csv file
with open('comments.csv', 'r') as file:
    reader = csv.reader(file)
    header_2 = next(reader)
    
    # add column name to first column
    if not header_2[0]:
        header_2[0] = 'Index'
    
    # replace space with _ in column names
    header_2 = [col.replace(' ', '_') for col in header_2]
    header_2[0] = f'"{header_2[0]}"'

    # create table with column names and data types
    create_table_query = f'''
        CREATE TABLE IF NOT EXISTS comments (
            {header_2[0]} INTEGER,
            {header_2[1]} VARCHAR,
            {header_2[2]} TEXT,
            {header_2[3]} FLOAT,
            {header_2[4]} FLOAT,
            FOREIGN KEY ({header_2[1]}) REFERENCES videos_stats({header_2[1]})
        )
    '''

    # execute query
    cursor.execute(create_table_query)

In [68]:
# Input data from csv file
with open('comments.csv', 'r') as file:
    reader = csv.reader(file)
    next(reader)

    # create strings for insert queries
    # concatenate column names with ', ' as separator
    columns = ', '.join(header_2)
    # concatenate len(header) of '?' with ', ' as separator
    question_marks = ', '.join(['?'] * len(header_2))

    # insert data
    for row in reader:
        insert_query = f'INSERT INTO comments ({columns}) VALUES ({question_marks})'
        cursor.execute(insert_query, row)
    
    # commit changes
    conn.commit()

In [69]:
# Print table
cursor.execute('SELECT * FROM comments')
#cursor.execute('PRAGMA table_info(comments)')
rows = cursor.fetchall()
for row in rows:
    print(row)

(0, 'wAZZ-UWGVHI', "Let's not forget that Apple Pay in 2014 required a brand new iPhone in order to use it.  A significant portion of Apple's user base wasn't able to use it even if they wanted to.  As each successive iPhone incorporated the technology and older iPhones were replaced the number of people who could use the technology increased.", 95.0, 1.0)
(1, 'wAZZ-UWGVHI', 'Here in NZ 50% of retailers don’t even have contactless credit card machines like pay-wave which support Apple Pay. They don’t like the high fees that come with these.', 19.0, 0.0)
(2, 'wAZZ-UWGVHI', "I will forever acknowledge this channel with the help of your lessons and ideas explanations, Now It's quite helpful while you'll just sit at your comfort and monitor your account Growth.", 161.0, 2.0)
(3, 'wAZZ-UWGVHI', 'Whenever I go to a place that doesn’t take Apple Pay (doesn’t happen too often), it’s such a drag. Between ‘contactless Covid’ habits and my getting the Apple Card, I’ve gotten so used to Apple Pay 

In [ ]:
cursor.close()
conn.close()

In [ ]:
#cursor.execute('''
#    DROP TABLE IF EXISTS videos_stats
#''')
#cursor.execute('''
#    DROP TABLE IF EXISTS comments
#''')
#
#conn.commit()

In [70]:
#cursor.execute('''
#    SELECT * FROM videos_stats
#    WHERE Likes = ''
#''')
#
#missing = cursor.fetchall()
#for row in missing:
#    print(row)